# Overview: MASTER DOCUMENT
- In this document, we highlight all of the steps necessary to produce a functioning folium map.
- Requirements:
    - All modules in the 'imports' cell below
    - CSV Files: (from /data/folium/)
        - covid_for_folium.csv
        - fire_for_folium_contained.csv
        - fire_for_folium_ongoing.csv
    - Access to OpenStreetMap API (given below)
    


# Imports

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

import requests
from pathlib import Path


from sklearn.preprocessing import StandardScaler, OneHotEncoder, LabelEncoder
from sklearn.neighbors import KNeighborsClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score, train_test_split, GridSearchCV
from sklearn.pipeline import make_pipeline
from sklearn.impute import SimpleImputer
from sklearn.compose import make_column_transformer
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier

import folium
from folium.plugins import MarkerCluster
from folium.raster_layers import ImageOverlay
#from scipy.ndimage import imread
import cv2 

# Inputs

In [2]:
golden_gate_coords = (-122.4783, 37.8199)
tahoe_coords = (-120.0324, 39.0968)
la_coords = (-118.2437, 34.0522)

start = golden_gate_coords 
stop = tahoe_coords
max_distance = 1.1
amenity = 'fuel'
amenity_name = 'yes'
see_covid_data = 'yes'
see_fire_data = 'yes'

covid_df = pd.read_csv('./data/folium/covid_for_folium.csv')
fire_df_contained = pd.read_csv('./data/folium/fire_for_folium_contained.csv')
fire_df_ongoing = pd.read_csv('./data/folium/fire_for_folium_ongoing.csv')

# Get Amenity data

In [3]:
def get_amenity_data(amenity):
    my_file = Path('./data/folium/amenities/'+str(amenity)+'.csv')
    if my_file.exists():
        amenity_df = pd.read_csv('./data/folium/amenities/'+str(amenity)+'.csv')
    else:
        query = '\n    [out:json];\n    area[name = "California"]->.search;\n    node[amenity='+str(amenity)+'](area.search);\n    out;\n'
        overpass_url = "http://overpass-api.de/api/interpreter"
        overpass_query = query
        response = requests.get(overpass_url, params={'data': overpass_query})
        # get names for each amenity location
        names = []
        for x in range(len(response.json()['elements'])):
            if 'name' in response.json()['elements'][x]['tags']:
                names.append(response.json()['elements'][x]['tags']['name'])
            else:
                names.append('Unknown Name')
        # get latitudes for each amenity location
        latitudes = []
        for x in range(len(response.json()['elements'])):
            latitudes.append(response.json()['elements'][x]['lat'])
        # get longitudes for each amenity location
        longitudes = []
        for x in range(len(response.json()['elements'])):
            longitudes.append(response.json()['elements'][x]['lon'])
        
        #create amenity df
        amenity_df = pd.DataFrame(data = list(zip(names, longitudes, latitudes)), columns = ['name', 'longitude', 'latitude'])
        
        amenity_df.to_csv('./data/folium/amenities/'+str(amenity)+'.csv', index = False)
    
    return amenity_df

# Create County column

First make model to predict county from latitude and longitude, based on covid_df data

In [4]:
le = LabelEncoder()
le.fit(covid_df['county'])

covid_df['county_encoded'] = le.transform(covid_df['county'])

X = covid_df[['longitude', 'latitude']]
y = covid_df['county_encoded']
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state = 22)

#these parameters are chosen from separate notebook's gridsearch
county_pipe = make_pipeline(StandardScaler(), KNeighborsClassifier(n_neighbors = 3))
county_pipe.fit(X_train, y_train)

Pipeline(steps=[('standardscaler', StandardScaler()),
                ('kneighborsclassifier', KNeighborsClassifier(n_neighbors=3))])

make amenity_df county column based on above

In [5]:
def get_counties(amenity_df_before_counties):
    amenity_df = amenity_df_before_counties
    X_amenity = amenity_df[['longitude', 'latitude']]
    amenity_df['county'] = list(le.inverse_transform(county_pipe.predict(X_amenity)))
    return amenity_df

# Risk predictions

## Model

In [6]:
X = covid_df[['longitude', 'latitude', 'county']]
y = covid_df['risk_category']

X_train, X_test, y_train, y_test = train_test_split(X, y, random_state = 22)

numeric_features = ['longitude', 'latitude']
numeric_transformer = make_pipeline(
    SimpleImputer(strategy = 'median'), 
    StandardScaler()
)

#catigorical vs numeric
categorical_features = ['county']
categorical_transformer = make_pipeline(
    SimpleImputer(strategy = 'constant', fill_value = 'missing'), 
    OneHotEncoder(handle_unknown = 'ignore')
)

column_transformer = make_column_transformer((categorical_transformer, categorical_features), 
                    (numeric_transformer, numeric_features), remainder = 'passthrough')

# Parameters chosen from Shiffraw's gridsearch
model_pipe = make_pipeline(column_transformer, SVC(C = .01, gamma = 1.0, kernel = 'rbf'))
#model_pipe = make_pipeline(column_transformer, LogisticRegression(max_iter = 1000, C = 10))

forest = RandomForestClassifier(max_depth=5, random_state=0, criterion='gini') 
model_pipe = make_pipeline(column_transformer, forest)
#I'm trying to run the SVM gridsearch again because I got a good score from it in the past.  But the parameters were C = .01, gamma = 1.0 and kernel was rbf.

model_pipe.fit(X_train, y_train)

Pipeline(steps=[('columntransformer',
                 ColumnTransformer(remainder='passthrough',
                                   transformers=[('pipeline-1',
                                                  Pipeline(steps=[('simpleimputer',
                                                                   SimpleImputer(fill_value='missing',
                                                                                 strategy='constant')),
                                                                  ('onehotencoder',
                                                                   OneHotEncoder(handle_unknown='ignore'))]),
                                                  ['county']),
                                                 ('pipeline-2',
                                                  Pipeline(steps=[('simpleimputer',
                                                                   SimpleImputer(strategy='median')),
                                        

## Amenity Risk Predictions

In [7]:
def get_risk_predictions(amenity_df_before_counties):
    amenity_df = get_counties(amenity_df_before_counties = amenity_df_before_counties)
    
    X_amenity = amenity_df[['longitude', 'latitude', 'county']]
    amenity_df['risk'] = model_pipe.predict(X_amenity)
    amenity_df['risk'] = amenity_df['risk'].map({0: 'Low Risk', 1: 'Medium Risk', 2: 'High Risk', 3: 'Very High Risk'})
    
    return amenity_df

# Folium: no Ellipse

In [31]:
cal_coordinates = (36.7783, -119.4179)
def display_folium_no_ellipse_yescovid_yesfire(amenity_df_input):#, img_name):
    """
    display the folium map of amenities and their associated risk values
    
    In order to implement the ellipse visualization functionality discussed below, 
    uncomment all lines in this function that are not surrounded by triple asterisks (***)
    
    The ellipse function isn't working very well though, I still have to fix some bugs.
    
    """
    #***Dataframes separated by risk***
    amenity_df = amenity_df_input
    lowrisk_df = amenity_df.loc[amenity_df['risk'] == 'Low Risk']
    mediumrisk_df = amenity_df.loc[amenity_df['risk'] == 'Medium Risk']
    highrisk_df = amenity_df.loc[amenity_df['risk'] == 'High Risk']
    veryhighrisk_df = amenity_df.loc[amenity_df['risk'] == 'Very High Risk']
    
    #lowrisk_df_in_ellipse = lowrisk_df.loc[lowrisk_df['in_ellipse'] == 1]
    #image_name = './data/folium/'+img_name+'.png'
    
    if lowrisk_df.empty:
        print('please expand your search range')
    else:
        folium_map = folium.Map(location=cal_coordinates, zoom_start=10, tiles='CartoDB Positron')
        #***with fire***
        for row in fire_df_contained.iterrows():
            row_values = row[1]
            location = [row_values['latitude'], row_values['longitude']]
            popup = popup ='<strong>' + str(row_values['name_fire']) + ': ' + str(row_values['status']) + '</strong>'
            marker = folium.Circle(location=location,fill = True, fillOpacity = 1, color = 'orange', weight = 0, opacity = .8, radius=row_values['radius'], popup=popup, tooltip='Click here to see more information')
            marker.add_to(folium_map)
            
        for row in fire_df_ongoing.iterrows():
            row_values = row[1]
            location = [row_values['latitude'], row_values['longitude']]
            popup = popup ='<strong>' + str(row_values['name_fire']) + ': ' + str(row_values['status']) + '</strong>'
            marker = folium.Circle(location=location,fill = True, fillOpacity = 1, color = 'red', weight = 0, opacity = .8, radius=row_values['radius'], popup=popup, tooltip='Click here to see more information')
            marker.add_to(folium_map)
        
        #***with covid***
        for row in covid_df.iterrows():
            row_values = row[1]
            location = [row_values['latitude'], row_values['longitude']]
            popup = popup ='<strong>' + 'Total Cases: '+ str(row_values['radius']) + '</strong>'
            marker = folium.Circle(location=location,fill = True, fillOpacity = 1, color = 'blue', weight = 0, opacity = .8, radius=row_values['radius'], popup=popup, tooltip='Click here to see more information')
            marker.add_to(folium_map)

        #***with amenity***
        for row in lowrisk_df.iterrows():
            row_values = row[1]
            location = [row_values['latitude'], row_values['longitude']]
            popup = popup ='<strong>' + str(row_values['name']) + ': ' + str(row_values['risk']) + '</strong>'
            marker = folium.Circle(location=location,fill = True, fillOpacity = 1, color = 'green', weight = 1, opacity = .8, radius=1, popup=popup, tooltip='Click here to see more information')
            marker.add_to(folium_map)
            
        for row in mediumrisk_df.iterrows():
            row_values = row[1]
            location = [row_values['latitude'], row_values['longitude']]
            popup = popup ='<strong>' + str(row_values['name']) + ': ' + str(row_values['risk']) + '</strong>'
            marker = folium.Circle(location=location,fill = True, fillOpacity = 1, color = 'yellow', weight = 1, opacity = .8, radius=1, popup=popup, tooltip='Click here to see more information')
            marker.add_to(folium_map)
            
        for row in highrisk_df.iterrows():
            row_values = row[1]
            location = [row_values['latitude'], row_values['longitude']]
            popup = popup ='<strong>' + str(row_values['name']) + ': ' + str(row_values['risk']) + '</strong>'
            marker = folium.Circle(location=location,fill = True, fillOpacity = 1, color = 'orange', weight = 1, opacity = .8, radius=1, popup=popup, tooltip='Click here to see more information')
            marker.add_to(folium_map)
            
        for row in veryhighrisk_df.iterrows():
            row_values = row[1]
            location = [row_values['latitude'], row_values['longitude']]
            popup = popup ='<strong>' + str(row_values['name']) + ': ' + str(row_values['risk']) + '</strong>'
            marker = folium.Circle(location=location,fill = True, fillOpacity = 1, color = 'red', weight = 1, opacity = .8, radius=1, popup=popup, tooltip='Click here to see more information')
            marker.add_to(folium_map)
        
        #for row in lowrisk_df_in_ellipse.iterrows():
            #row_values = row[1]
            #marker = folium.Marker(location = [row_values['latitude'], row_values['longitude']], clustered_marker = True)
            #marker.add_to(folium_map)

        #img = cv2.imread(image_name)
        #folium_map.add_child(ImageOverlay(img, opacity=0.4, bounds =[[32.5504761, -124.28758], [41.9643067, -114.5703842]]))
        
        display(folium_map)

# All together, now

In [35]:
def display_map(amenity):
    amenities_df = get_amenity_data(amenity = amenity)
    amenities_df_2 = get_risk_predictions(amenity_df_before_counties = amenities_df)
    display_folium_no_ellipse_yescovid_yesfire(amenity_df_input = amenities_df_2)

In [23]:
amenity_input = input("Enter your desired amenity: ") 
display_map(amenity = str(amenity_input))

Enter your desired amenity:  fuel


# Future Directions: Mapping given trip destinations
- More information available in 'draft_code/regions_viz.ipynb'

### Is the target point within range?
- The 'range' is whatever is in the ellipse shown below, with the major axis representing the distance from your start and ending points
<center>
 <img src="./pics/Ellipse.png" alt="drawing" width="400"/>
</center>
- In this ellipse, the perimeter represents the points at which your path has the same length.
<center>
 <img src="./pics/p1_ellipse.png" alt="drawing" width="400"/>
 <img src="./pics/p2_ellipse.png" alt="drawing" width="400"/>
</center>

### Ellipse rotations
- where (xp, yp) are the point coordinates and (x0, y0) is the center of the ellipse
- where a is the minor axis and b is the major axis
<center>
 <img src="./pics/ellipse_eq.png" alt="drawing" width="800"/>
</center>

In [26]:
from matplotlib.patches import Ellipse

# Functions:
- **start_end_line**: given some start and stop point, determine and visualize the linear equation to connect them. Return tuple of (list of x components to plot, list of y components to plot)
- **get_midpoint**: Find the midpoint between two points. Return the midpoint coordinates.
- **angle_from_x_axis**: Given two points, find the angle their connecting line makes with the x axis. Returns theta in radians.
- **rotate_point**: Given a point, a center of rotation, and an angle to rotate (positive counterclockwise direction, in radians), return the coordinates of the rotated point.
- **is_in_ellipse**: Given a starting point, a stopping point, the maximum distance someone is willing to travel beyond their given itinerary, and a dataframe of the locations of amenities that they are interested in stopping at. Returns the same dataframe of points, except with an extra column where '0' means the location is not within the ellipse, and '1' means the location is in the ellipse. Also returns the start point, stop point, major_axis of the ellipse, minor_axis of the ellipse, and the rotated angle theta in degrees.
- **show_amenity_ellipse**: Given the output of **is_in_ellipse**, show a scatter plot of all of the amenities within this range. The color code is based on the covid safety rating.
- **get_ellipse_image**: Given the output of **is_in_ellipse**, save an image of the ellipse shown in **show_amenity_ellipse**, but ONLY the ellipse, NOT the amenities! This function is useful for folium implementation.

Although the folium detection is not working accurately yet with this implementation, this is the general idea of what it would look like if you were traveling between San Fransisco and  Lake Tahoe:
<center>
 <img src="./pics/not_folium_pic.png" alt="drawing" width="600"/>
</center>

However, because of some ellipse compression rotation issues, it ends ub being a scooch off when you try to implement the image overlay. Below is an example of the image overlay when you input the starting and stopping locations as LA and Lake Tahoe, finding gas stations on the way:
<center>
 <img src="./pics/folium_pic.png" alt="drawing" width="800"/>
</center>

In other drafts, the marker feature (locating markers for gas stations of low risk in the area) was working just fine, but isn't here for some reason.

In [27]:
def start_end_line(start, end):
    slope = (start[1] - end[1]) / (start[0] - end[0])
    b = start[1] - (slope * start[0])
    x = np.linspace(start[0], end[0])
    y = slope * x + b
    return (x, y)


def get_midpoint(start, stop):
    delta_x = stop[0] + start[0]
    delta_y = stop[1] + start[1]
    if delta_x == 0:
        midpoint_x = start[0]
    else:
        midpoint_x = delta_x / 2
    if delta_y == 0:
        midpoint_y = start[1]
    else:
        midpoint_y = delta_y / 2
    return (midpoint_x, midpoint_y)


def angle_from_x_axis(start, stop):
    delta_x = start[0] - stop[0]
    delta_y = start[1] - stop[1]
    theta = np.arctan(delta_y / delta_x)
    return theta


def rotate_point(point, center_of_rotation, angle_positive_counterclockwise_radians):
    x_0 = point[0]
    y_0 = point[1]
    
    x_c = center_of_rotation[0]
    y_c = center_of_rotation[1]
    
    theta = angle_positive_counterclockwise_radians
    
    cos = np.cos(theta)
    sin = np.sin(theta)
    
    x_1 = (cos * (x_0 - x_c)) - (sin * (y_0 - y_c)) + x_c
    y_1 = (sin * (x_0 - x_c)) + (cos * (y_0 - y_c)) + y_c
    
    return (x_1, y_1)

def is_in_ellipse(start, stop, max_distance, df):
    
    midpoint = get_midpoint(start = start, stop = stop)
    target_list = list(zip(df['longitude_gas'], df['latitude_gas']))
    
    
    # transform all points so midpoint is centered
    start_translated = (start[0] - midpoint[0], start[1] - midpoint[1])
    stop_translated = (stop[0] - midpoint[0], stop[1] - midpoint[1])
    
    targets_translated = []
    for x in range(len(target_list)):
        target_translated = (target_list[x][0] - midpoint[0], target_list[x][1] - midpoint[1])
        targets_translated.append(target_translated)
    
    
    theta = angle_from_x_axis(start = start, stop = stop)
    theta_degrees = theta * 180 / np.pi
    start_rotated = rotate_point(point = start_translated, center_of_rotation = (0, 0), angle_positive_counterclockwise_radians = -theta)
    stop_rotated = rotate_point(point = stop_translated, center_of_rotation = (0, 0), angle_positive_counterclockwise_radians = -theta)
    
    target_list_rotated = []
    for x in range(len(targets_translated)):
        target_point = targets_translated[x]
        target_point_rotated = rotate_point(point = target_point, center_of_rotation = (0, 0), angle_positive_counterclockwise_radians = -theta)
        target_list_rotated.append(target_point_rotated)
    
    # define the major an minor axis
    delta_x_rotated = stop_rotated[0] - start_rotated[0]
    delta_y_rotated = stop_rotated[1] - start_rotated[1] # should always be zero
    
    major_axis = delta_x_rotated * max_distance # a + b
    minor_axis = major_axis * np.sqrt(max_distance**2 - 1) # formula below
    
    # see which points are in ellipse
    in_ellipse = []
    for x in range(len(target_list_rotated)):
        x_target = target_list_rotated[x][0]
        y_target = target_list_rotated[x][1]
        
        component1 = (x_target / (major_axis/2))**2
        component2 = (y_target / (minor_axis/2))**2
        
        if component1 + component2 <= 1:
            in_ellipse.append('1')
        else:
            in_ellipse.append('0')
        #in_ellipse.append(str(component1 + component2))
        #in_ellipse.append((x_target, y_target))
    
    mapped = [int(x) for x in in_ellipse]
    
    df['in_ellipse'] = mapped
    
    return df, start, stop, major_axis, minor_axis, theta_degrees
    #return theta_degrees

In [28]:
def show_amenity_ellipse(result_from_isinellipse_function):
    result = result_from_isinellipse_function
    df = result[0]
    start = result[1]
    stop = result[2]
    major_axis = result[3]
    minor_axis = result[4]
    theta_degrees = result[5]
    
    df_zeros = df.loc[df['in_ellipse'] == 0]
    df_ones = df.loc[df['in_ellipse'] == 1]
    
    plt.figure(figsize=(12, 12))
    ellipse = Ellipse(xy = get_midpoint(start, stop), width = major_axis, height = minor_axis, angle = theta_degrees, alpha = .4)
    plt.gca().add_patch(ellipse)
    plt.scatter(df_zeros['longitude_gas'], df_zeros['latitude_gas'], marker = 'o', c = df_zeros['rating'])
    plt.scatter(df_ones['longitude_gas'], df_ones['latitude_gas'], marker = "^", c = df_ones['rating'])
    plt.show()

In [32]:
def get_ellipse_image(result_from_isinellipse_function, img_name):
    result = result_from_isinellipse_function
    df = result[0]
    start = result[1]
    stop = result[2]
    major_axis = result[3]
    minor_axis = result[4]
    theta_degrees = result[5]
    
    #these represent the california coordinate extrema, which will be used as a baseline for easier folium implementation
    graph_xmin = -124.28758
    graph_xmax = -114.5703842
    graph_ymin = 32.5504761
    graph_ymax = 41.9643067
    
    ellipse = Ellipse(xy = get_midpoint(start, stop), width = major_axis, height = minor_axis, angle = theta_degrees, alpha = .4)
    plt.gca().add_patch(ellipse)
    plt.xlim(graph_xmin, graph_xmax)
    plt.ylim(graph_ymin, graph_ymax)
    plt.axis("off")
    
    plt.savefig('./data/folium/'+img_name+'.png')

# Run this instead if you want to visualize amenities between two points
#### If you have a starting and stopping point, and a max amount of time you're willing to tack on to your trip

In [34]:
def display_map_given_path(amenity, start, stop, max_distance):
    
    amenities_df = get_amenity_data(amenity = amenity)
    amenities_df_2 = get_risk_predictions(amenity_df_before_counties = amenities_df)
    
    # to run these two lines, need to make sure the necessary code is in the display_folium_no_ellipse_yescovid_yesfire function
    result = is_in_ellipse(start = start, stop = stop, max_distance = max_distance, df = amenities_df_2)
    #need this to run before the next line so that the image saves
    get_ellipse_image(result_from_isinellipse_function = result, img_name = amenity)
    
    display_folium_no_ellipse_yescovid_yesfire(amenity_df_input = amenities_df_2, img_name = amenity)

In [36]:
amenity_input = input("Enter your desired amenity: ") 
start_input = input("Enter your starting coordinates: ") 
stop_input = input("Enter your ending coordinates: ") 
max_distance_input = input("Enter the max percentage of extra time that you are willing to take: ") 

max_distance_calculated = 1 + (max_distance_input/100)

display_map_given_path(amenity = amenity_input, start = start_input, stop = stop_input, max_distance = max_distance_calculated)

KeyboardInterrupt: Interrupted by user